In [ ]:
from utils.metrics import metric
from data_provider.data_loader import Dataset_Custom
from models import xPatch
from utils.tools import EarlyStopping, adjust_learning_rate, visual
from data_provider.data_factory import data_provider
from exp.exp_main import Exp_Main
import sys
import os
import time
import warnings
import math
import argparse
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from torch import optim
from torch.utils.data import DataLoader
from sklearn.preprocessing import StandardScaler

warnings.filterwarnings('ignore')

project_root = os.path.abspath('./')
if project_root not in sys.path:
    sys.path.append(project_root)

In [16]:
class Args:
    def __init__(self):
        self.is_training = 1
        self.train_only = False
        self.model_id = 'ETTh1_Pred_Notebook_Untuned'
        self.model = 'xPatch'

        self.data = 'custom'
        self.scale = True
        self.root_path = './data/'
        # self.data_path = 'aapl_OHLCV.csv'
        self.data_path = 'ETTh1.csv'
        self.features = 'MS'  # Multiple Features, Single target
        # self.target = 'Close' # The target feature
        self.target = 'OT'  # The target feature
        self.freq = 'h'
        self.checkpoints = './checkpoints/'
        self.embed = 'timeF'

####################################################################################################################################################
# Hyperparameter Tuning
        # Forecasting Task
        self.seq_len = 48
        self.label_len = 48
        self.pred_len = 5
        self.enc_in = 7  # Ensure this matches the number of features in the CSV after 'date'

        # Patching
        self.patch_len = 12
        self.stride = 6
        self.padding_patch = 'end'

        # Moving Average
        self.ma_type = 'ema'
        self.alpha = 0.2
        self.beta = 0.2

        # Optimization
        self.num_workers = 8  # Adjust based on your system
        self.itr = 1
        self.train_epochs = 3
        self.batch_size = 16
        self.patience = 15
        self.learning_rate = 0.0001
        self.des = 'Notebook_Run_MS'
        self.loss = 'mae'
        self.lradj = 'type1'  # learning rate strategy
        self.revin = 1
####################################################################################################################################################

        # GPU
        self.use_gpu = True if torch.cuda.is_available() else False
        self.gpu = 0
        self.use_multi_gpu = False
        self.devices = '0'
        self.test_flop = False

####################################################################################################################################################

        # Wandb configuration
        self.use_wandb = True  # Enable/disable wandb logging
        # Team name
        self.wandb_entity = 'xplstm'
        # Project name
        self.wandb_project = 'CS7643-GroupProject'
        # Run-specific notes
        self.experiment_notes = 'LSTM head after patching layer'

####################################################################################################################################################
        # Add missing xPatch parameters
        self.d_model = 128
        self.d_ff = 256
        self.e_layers = 3
        self.dropout = 0.1
        self.k = 3
        self.decomp = 0

####################################################################################################################################################

        # Optimized LSTM Configuration for Network Layer
        self.use_lstm = True                    # Enable LSTM in Network
        self.lstm_hidden_size = 192              # Optimal hidden size
        self.lstm_layers = 4                    # Deep enough for temporal modeling
        self.lstm_dropout = 0.2                # Regularization
        self.lstm_bidirectional = True          # Better context understanding

        # Note: use_lstm_attention is removed since we're using LSTM in Network layer instead

####################################################################################################################################################


args = Args()

if not os.path.exists(args.checkpoints):
    os.makedirs(args.checkpoints)

In [17]:
# Directional Prediction Configuration
class DirectionalArgs(Args):
    def __init__(self):
        super().__init__()

        # Override for directional prediction
        self.model_id = 'ETTh1_Directional_Test'
        self.des = 'Directional_Prediction_Test'

        # Directional prediction configuration
        self.directional_mode = True                    # Enable directional prediction
        # 'classification', 'penalty', or 'hybrid'
        self.directional_loss_type = 'penalty'
        # 2 (up/down) or 3 (up/neutral/down)
        self.num_direction_classes = 3
        # Threshold for neutral class (0.5% change)
        self.direction_threshold = 0.005
        self.directional_penalty_weight = 1.5          # Weight for directional penalty
        self.directional_base_loss = 'mae'             # Base loss for penalty mode

        # Adjust training for directional focus
        # More epochs for directional learning
        self.train_epochs = 3
        self.learning_rate = 0.0005                    # Slightly higher learning rate
        # More patience for directional convergence
        self.patience = 20

        print(f"🎯 Directional Configuration:")
        print(f"   Mode: {self.directional_loss_type}")
        print(
            f"   Classes: {self.num_direction_classes} ({'Up/Down' if self.num_direction_classes == 2 else 'Up/Neutral/Down'})")
        print(
            f"   Threshold: {self.direction_threshold:.3f} ({self.direction_threshold*100:.1f}%)")
        print(f"   Penalty Weight: {self.directional_penalty_weight}")


# Create directional args instance
args_directional = DirectionalArgs()

🎯 Directional Configuration:
   Mode: penalty
   Classes: 3 (Up/Neutral/Down)
   Threshold: 0.005 (0.5%)
   Penalty Weight: 1.5


In [23]:
# Directional Inference and Evaluation Functions
def price_to_direction_classes(prices, last_prices, threshold=0.01, num_classes=3):
    """Convert prices to direction classes"""
    # Calculate changes from last known price
    # Broadcast last_prices to match prices
    changes = prices - last_prices.unsqueeze(1)

    if num_classes == 3:
        directions = torch.ones_like(changes, dtype=torch.long)  # neutral (1)
        directions[changes > threshold] = 2  # up
        directions[changes < -threshold] = 0  # down
    else:
        directions = (changes > 0).long()  # binary up/down

    return directions


def directional_inference(model, data_loader, args):
    """
    Perform directional inference and calculate directional metrics
    """
    model.eval()
    directions_pred = []
    directions_true = []
    prices_pred = []
    prices_true = []
    last_values_all = []

    print("🔍 Running directional inference...")

    with torch.no_grad():
        for i, (batch_x, batch_y, batch_x_mark, batch_y_mark) in enumerate(data_loader):
            if args.use_gpu:
                batch_x = batch_x.cuda()
                batch_y = batch_y.cuda()

            # Get last known price for direction calculation
            last_values = batch_x[:, -1, :]  # [batch, channels]

            # Model prediction (always returns prices in current setup)
            pred_prices = model(batch_x)  # [batch, pred_len, channels]

            # Convert price predictions to directions
            pred_classes = price_to_direction_classes(
                pred_prices, last_values,
                threshold=getattr(args, 'direction_threshold', 0.01),
                num_classes=getattr(args, 'num_direction_classes', 3)
            )

            # True directions
            true_classes = price_to_direction_classes(
                batch_y, last_values,
                threshold=getattr(args, 'direction_threshold', 0.01),
                num_classes=getattr(args, 'num_direction_classes', 3)
            )

            # Store results
            directions_pred.append(pred_classes.cpu().numpy())
            directions_true.append(true_classes.cpu().numpy())
            prices_pred.append(pred_prices.cpu().numpy())
            prices_true.append(batch_y.cpu().numpy())
            last_values_all.append(last_values.cpu().numpy())

            if i % 10 == 0:
                print(f"   Processed {i+1}/{len(data_loader)} batches")

    # Concatenate all results
    directions_pred = np.concatenate(directions_pred, axis=0)
    directions_true = np.concatenate(directions_true, axis=0)
    prices_pred = np.concatenate(prices_pred, axis=0)
    prices_true = np.concatenate(prices_true, axis=0)
    last_values_all = np.concatenate(last_values_all, axis=0)

    return {
        'directions_pred': directions_pred,
        'directions_true': directions_true,
        'prices_pred': prices_pred,
        'prices_true': prices_true,
        'last_values': last_values_all
    }


def evaluate_directional_performance(results, args):
    """
    Evaluate directional prediction performance
    """
    directions_pred = results['directions_pred']
    directions_true = results['directions_true']
    prices_pred = results['prices_pred']
    prices_true = results['prices_true']

    # Overall directional accuracy
    correct_directions = (directions_pred == directions_true)
    overall_accuracy = correct_directions.mean()

    # Per-timestep accuracy
    timestep_accuracy = correct_directions.mean(
        axis=(0, 2))  # Average over batch and channels

    # Per-channel accuracy
    channel_accuracy = correct_directions.mean(
        axis=(0, 1))  # Average over batch and timesteps

    # Class-wise accuracy
    num_classes = getattr(args, 'num_direction_classes', 3)
    class_names = ['Down', 'Neutral',
                   'Up'] if num_classes == 3 else ['Down', 'Up']
    class_accuracy = {}

    for class_idx in range(num_classes):
        mask = (directions_true == class_idx)
        if mask.sum() > 0:
            class_accuracy[class_names[class_idx]
                           ] = correct_directions[mask].mean()
        else:
            class_accuracy[class_names[class_idx]] = 0.0

    # Trend consistency (3+ consecutive same direction)
    trend_consistency = calculate_trend_consistency(
        directions_pred, directions_true, min_trend_length=3
    )

    # Trading simulation metrics
    trading_metrics = calculate_trading_metrics(
        directions_pred, prices_pred, prices_true, results['last_values']
    )

    return {
        'overall_accuracy': overall_accuracy,
        'timestep_accuracy': timestep_accuracy,
        'channel_accuracy': channel_accuracy,
        'class_accuracy': class_accuracy,
        'trend_consistency': trend_consistency,
        'trading_metrics': trading_metrics
    }


def calculate_trend_consistency(directions_pred, directions_true, min_trend_length=3):
    """Calculate how well the model captures sustained trends"""
    batch_size, pred_len, channels = directions_pred.shape

    if pred_len < min_trend_length:
        return 0.0

    trend_matches = 0
    total_trends = 0

    for b in range(batch_size):
        for c in range(channels):
            for start in range(pred_len - min_trend_length + 1):
                end = start + min_trend_length

                true_trend = directions_true[b, start:end, c]
                pred_trend = directions_pred[b, start:end, c]

                # Check if it's a sustained trend (all same direction, not neutral)
                # 1 is neutral
                if len(np.unique(true_trend)) == 1 and true_trend[0] != 1:
                    total_trends += 1
                    if np.array_equal(true_trend, pred_trend):
                        trend_matches += 1

    return trend_matches / total_trends if total_trends > 0 else 0.0


def calculate_trading_metrics(directions_pred, prices_pred, prices_true, last_values):
    """Calculate trading simulation metrics"""
    batch_size, pred_len, channels = directions_pred.shape

    # Simple trading strategy: buy on predicted up, sell on predicted down
    returns = []
    hit_rates = []

    for b in range(batch_size):
        for c in range(channels):
            for t in range(pred_len):
                if t == 0:
                    prev_price = last_values[b, c]
                else:
                    prev_price = prices_true[b, t-1, c]

                current_price = prices_true[b, t, c]
                actual_return = (current_price - prev_price) / prev_price

                # Trading signal based on prediction
                if directions_pred[b, t, c] == 2:  # Predicted up
                    trade_return = actual_return  # Buy
                elif directions_pred[b, t, c] == 0:  # Predicted down
                    trade_return = -actual_return  # Sell
                else:  # Neutral or binary down
                    trade_return = 0  # No trade

                returns.append(trade_return)
                hit_rates.append(1 if trade_return > 0 else 0)

    avg_return = np.mean(returns) if returns else 0
    hit_rate = np.mean(hit_rates) if hit_rates else 0
    sharpe_ratio = avg_return / \
        np.std(returns) if returns and np.std(returns) > 0 else 0

    return {
        'avg_return': avg_return,
        'hit_rate': hit_rate,
        'sharpe_ratio': sharpe_ratio,
        'total_trades': len(returns)
    }


print("✅ Created directional inference and evaluation functions")
print("📊 Capabilities:")
print("   - Price-to-direction conversion")
print("   - Directional accuracy calculation")
print("   - Trend consistency analysis")
print("   - Trading simulation metrics")
print("   - Per-class and per-timestep analysis")

✅ Created directional inference and evaluation functions
📊 Capabilities:
   - Price-to-direction conversion
   - Directional accuracy calculation
   - Trend consistency analysis
   - Trading simulation metrics
   - Per-class and per-timestep analysis


In [24]:
# Directional Training and Testing Workflow
print("🎯 Starting Directional Prediction Training...")
print("=" * 60)

# Train with directional loss
exp_directional = Exp_Main(args_directional)
print(
    f"🔧 Directional Args: {args_directional.directional_loss_type} mode, {args_directional.num_direction_classes} classes")

# Train the model
best_model = exp_directional.train(args_directional.model_id)

# Test the model (standard testing)
print("\n📊 Running standard test evaluation...")
exp_directional.test(args_directional.model_id)

# Load test data for directional evaluation
print("\n🎯 Running directional evaluation...")
test_data, test_loader = data_provider(args_directional, flag='test')

# Perform directional inference
directional_results = directional_inference(
    best_model, test_loader, args_directional)

# Evaluate directional performance
performance = evaluate_directional_performance(
    directional_results, args_directional)

# Print results
print("\n" + "=" * 60)
print("🎯 DIRECTIONAL PREDICTION RESULTS")
print("=" * 60)

print(f"\n📈 Overall Performance:")
print(
    f"   Directional Accuracy: {performance['overall_accuracy']:.4f} ({performance['overall_accuracy']*100:.2f}%)")
print(
    f"   Trend Consistency: {performance['trend_consistency']:.4f} ({performance['trend_consistency']*100:.2f}%)")

print(f"\n📊 Per-Class Accuracy:")
for class_name, accuracy in performance['class_accuracy'].items():
    print(f"   {class_name}: {accuracy:.4f} ({accuracy*100:.2f}%)")

print(f"\n⏰ Per-Timestep Accuracy:")
for t, accuracy in enumerate(performance['timestep_accuracy']):
    print(f"   Step {t+1}: {accuracy:.4f} ({accuracy*100:.2f}%)")

print(f"\n💰 Trading Simulation:")
trading = performance['trading_metrics']
print(
    f"   Average Return: {trading['avg_return']:.4f} ({trading['avg_return']*100:.2f}%)")
print(
    f"   Hit Rate: {trading['hit_rate']:.4f} ({trading['hit_rate']*100:.2f}%)")
print(f"   Sharpe Ratio: {trading['sharpe_ratio']:.4f}")
print(f"   Total Trades: {trading['total_trades']:,}")

print(f"\n🔍 Per-Channel Performance:")
for c, accuracy in enumerate(performance['channel_accuracy']):
    print(f"   Channel {c+1}: {accuracy:.4f} ({accuracy*100:.2f}%)")

# Compare with random baseline
random_accuracy = 1.0 / args_directional.num_direction_classes
improvement = (performance['overall_accuracy'] -
               random_accuracy) / random_accuracy * 100

print(f"\n🎲 Baseline Comparison:")
print(
    f"   Random Accuracy: {random_accuracy:.4f} ({random_accuracy*100:.2f}%)")
print(f"   Model Improvement: {improvement:.1f}% above random")

🎯 Starting Directional Prediction Training...
Use CPU


🎯 Starting Directional Prediction Training...
Use CPU


🎯 Starting Directional Prediction Training...
Use CPU


🔧 Directional Args: penalty mode, 3 classes
train 12142
val 1738
test 3480
	iters: 100, epoch: 1 | loss: 0.0962529
	speed: 0.0708s/iter; left time: 153.9151s
	iters: 100, epoch: 1 | loss: 0.0962529
	speed: 0.0708s/iter; left time: 153.9151s
	iters: 200, epoch: 1 | loss: 0.0701634
	speed: 0.0741s/iter; left time: 153.8530s
	iters: 200, epoch: 1 | loss: 0.0701634
	speed: 0.0741s/iter; left time: 153.8530s
	iters: 300, epoch: 1 | loss: 0.0793333
	speed: 0.0736s/iter; left time: 145.3266s
	iters: 300, epoch: 1 | loss: 0.0793333
	speed: 0.0736s/iter; left time: 145.3266s
	iters: 400, epoch: 1 | loss: 0.0770629
	speed: 0.0704s/iter; left time: 131.9856s
	iters: 400, epoch: 1 | loss: 0.0770629
	speed: 0.0704s/iter; left time: 131.9856s
	iters: 500, epoch: 1 | loss: 0.0775866
	speed: 0.0682s/iter; left time: 121.0068s
	iters: 500, epoch: 1 | loss: 0.0775866
	speed: 0.0682s/iter; left time: 121.0068s
	iters: 600, epoch: 1 | loss: 0.0887342
	speed: 0.0704s/iter; left time: 117.8884s
	iters: 600,

🎯 Starting Directional Prediction Training...
Use CPU


...


🎯 Running directional evaluation...
test 3480
🔍 Running directional inference...
   Processed 1/217 batches
   Processed 11/217 batches
   Processed 1/217 batches
   Processed 11/217 batches
   Processed 21/217 batches
   Processed 31/217 batches
   Processed 21/217 batches
   Processed 31/217 batches


🎯 Starting Directional Prediction Training...
Use CPU


🔧 Directional Args: penalty mode, 3 classes
train 12142
val 1738
test 3480
	iters: 100, epoch: 1 | loss: 0.0962529
	speed: 0.0708s/iter; left time: 153.9151s
	iters: 100, epoch: 1 | loss: 0.0962529
	speed: 0.0708s/iter; left time: 153.9151s
	iters: 200, epoch: 1 | loss: 0.0701634
	speed: 0.0741s/iter; left time: 153.8530s
	iters: 200, epoch: 1 | loss: 0.0701634
	speed: 0.0741s/iter; left time: 153.8530s
	iters: 300, epoch: 1 | loss: 0.0793333
	speed: 0.0736s/iter; left time: 145.3266s
	iters: 300, epoch: 1 | loss: 0.0793333
	speed: 0.0736s/iter; left time: 145.3266s
	iters: 400, epoch: 1 | loss: 0.0770629
	speed: 0.0704s/iter; left time: 131.9856s
	iters: 400, epoch: 1 | loss: 0.0770629
	speed: 0.0704s/iter; left time: 131.9856s
	iters: 500, epoch: 1 | loss: 0.0775866
	speed: 0.0682s/iter; left time: 121.0068s
	iters: 500, epoch: 1 | loss: 0.0775866
	speed: 0.0682s/iter; left time: 121.0068s
	iters: 600, epoch: 1 | loss: 0.0887342
	speed: 0.0704s/iter; left time: 117.8884s
	iters: 600,


🎯 Running directional evaluation...
test 3480
🔍 Running directional inference...
   Processed 1/217 batches
   Processed 11/217 batches
   Processed 1/217 batches
   Processed 11/217 batches
   Processed 21/217 batches
   Processed 31/217 batches
   Processed 21/217 batches
   Processed 31/217 batches


AttributeError: 'NoneType' object has no attribute '_log'

In [21]:
# Directional Prediction Visualization and Comparison
import matplotlib.pyplot as plt


def visualize_directional_predictions(results, args, sample_idx=0, channel_idx=0):
    """Visualize directional predictions vs actual"""

    directions_pred = results['directions_pred']
    directions_true = results['directions_true']
    prices_pred = results['prices_pred']
    prices_true = results['prices_true']
    last_values = results['last_values']

    pred_len = directions_pred.shape[1]
    num_classes = getattr(args, 'num_direction_classes', 3)
    class_names = ['Down', 'Neutral',
                   'Up'] if num_classes == 3 else ['Down', 'Up']
    colors = ['red', 'gray', 'green'] if num_classes == 3 else ['red', 'green']

    fig, ((ax1, ax2), (ax3, ax4)) = plt.subplots(2, 2, figsize=(15, 10))

    # 1. Price predictions vs actual
    ax1.plot(prices_true[sample_idx, :, channel_idx],
             'b-', label='Actual Prices', linewidth=2)
    ax1.plot(prices_pred[sample_idx, :, channel_idx],
             'r--', label='Predicted Prices', linewidth=2)
    ax1.axhline(y=last_values[sample_idx, channel_idx], color='gray',
                linestyle=':', alpha=0.7, label='Last Known Price')
    ax1.set_title(
        f'Price Predictions - Sample {sample_idx}, Channel {channel_idx}')
    ax1.set_ylabel('Price')
    ax1.legend()
    ax1.grid(True, alpha=0.3)

    # 2. Directional predictions vs actual
    x_pos = range(pred_len)
    width = 0.35

    pred_directions = directions_pred[sample_idx, :, channel_idx]
    true_directions = directions_true[sample_idx, :, channel_idx]

    ax2.bar([x - width/2 for x in x_pos], pred_directions,
            width, label='Predicted', alpha=0.7, color='orange')
    ax2.bar([x + width/2 for x in x_pos], true_directions,
            width, label='Actual', alpha=0.7, color='blue')
    ax2.set_title(
        f'Direction Predictions - Sample {sample_idx}, Channel {channel_idx}')
    ax2.set_ylabel('Direction Class')
    ax2.set_xlabel('Time Step')
    ax2.set_xticks(x_pos)
    ax2.set_xticklabels([f't+{i+1}' for i in x_pos])
    ax2.set_yticks(range(num_classes))
    ax2.set_yticklabels(class_names)
    ax2.legend()
    ax2.grid(True, alpha=0.3)

    # 3. Class distribution
    true_dist = [np.sum(directions_true == i) for i in range(num_classes)]
    pred_dist = [np.sum(directions_pred == i) for i in range(num_classes)]

    x_classes = range(num_classes)
    ax3.bar([x - width/2 for x in x_classes], true_dist,
            width, label='Actual', alpha=0.7, color='blue')
    ax3.bar([x + width/2 for x in x_classes], pred_dist, width,
            label='Predicted', alpha=0.7, color='orange')
    ax3.set_title('Overall Direction Class Distribution')
    ax3.set_ylabel('Count')
    ax3.set_xlabel('Direction Class')
    ax3.set_xticks(x_classes)
    ax3.set_xticklabels(class_names)
    ax3.legend()
    ax3.grid(True, alpha=0.3)

    # 4. Accuracy over time steps
    timestep_accuracy = []
    for t in range(pred_len):
        correct = (directions_pred[:, t, :] == directions_true[:, t, :]).mean()
        timestep_accuracy.append(correct)

    ax4.plot(range(1, pred_len + 1), timestep_accuracy,
             'g-o', linewidth=2, markersize=6)
    ax4.set_title('Directional Accuracy by Time Step')
    ax4.set_ylabel('Accuracy')
    ax4.set_xlabel('Time Step')
    ax4.set_xticks(range(1, pred_len + 1))
    ax4.set_xticklabels([f't+{i}' for i in range(1, pred_len + 1)])
    ax4.grid(True, alpha=0.3)
    ax4.set_ylim(0, 1)

    plt.tight_layout()
    plt.show()


def compare_regression_vs_directional(directional_performance=None):
    """Compare standard regression vs directional prediction"""

    print("\n" + "=" * 60)
    print("📊 REGRESSION vs DIRECTIONAL COMPARISON")
    print("=" * 60)

    # Load standard regression results
    standard_folder = f'./test_results/{args.model_id}/'
    directional_folder = f'./test_results/{args_directional.model_id}/'

    if os.path.exists(standard_folder + 'pred.npy'):
        standard_preds = np.load(standard_folder + 'pred.npy')
        standard_trues = np.load(standard_folder + 'true.npy')

        # Calculate standard regression metrics
        from utils.metrics import metric
        mae, mse = metric(standard_preds, standard_trues)

        print(f"\n🔢 Standard Regression Performance:")
        print(f"   MAE: {mae:.6f}")
        print(f"   MSE: {mse:.6f}")
        print(f"   RMSE: {np.sqrt(mse):.6f}")

        # Calculate directional accuracy for regression model
        test_data, test_loader = data_provider(args, flag='test')

        # Create standard experiment instance to get the model
        exp_standard = Exp_Main(args)
        # Load the trained model
        checkpoint_path = os.path.join(
            args.checkpoints, args.model_id, 'checkpoint.pth')
        if os.path.exists(checkpoint_path):
            exp_standard.model.load_state_dict(torch.load(checkpoint_path))
        else:
            print(
                "❌ Standard model checkpoint not found. Training standard model first...")
            return

        reg_directional_results = directional_inference(
            exp_standard.model,  # Standard model
            test_loader,
            args  # Standard args
        )
        reg_performance = evaluate_directional_performance(
            reg_directional_results, args)

        print(f"\n🎯 Standard Model - Directional Performance:")
        print(
            f"   Directional Accuracy: {reg_performance['overall_accuracy']:.4f} ({reg_performance['overall_accuracy']*100:.2f}%)")
        print(
            f"   Trend Consistency: {reg_performance['trend_consistency']:.4f}")

        # Only compare if directional performance is provided
        if directional_performance is not None:
            print(f"\n🎯 Directional Model - Performance:")
            print(
                f"   Directional Accuracy: {directional_performance['overall_accuracy']:.4f} ({directional_performance['overall_accuracy']*100:.2f}%)")
            print(
                f"   Trend Consistency: {directional_performance['trend_consistency']:.4f}")

            # Calculate improvement
            dir_improvement = ((directional_performance['overall_accuracy'] - reg_performance['overall_accuracy']) /
                               reg_performance['overall_accuracy'] * 100)
            trend_improvement = ((directional_performance['trend_consistency'] - reg_performance['trend_consistency']) /
                                 reg_performance['trend_consistency'] * 100 if reg_performance['trend_consistency'] > 0 else 0)

            print(f"\n📈 Improvement with Directional Loss:")
            print(f"   Directional Accuracy: {dir_improvement:+.1f}%")
            print(f"   Trend Consistency: {trend_improvement:+.1f}%")
        else:
            print(
                "\n⚠️ Directional model performance not provided. Run directional training first to compare.")

    else:
        print("❌ Standard regression results not found. Run standard training first.")

# Run visualization and comparison (will be executed after directional training)
# These will only work properly after running the directional training cell above


try:
    # Check if directional_results exists (from directional training cell)
    if 'directional_results' in locals():
        print("\n🎨 Generating directional prediction visualizations...")
        visualize_directional_predictions(
            directional_results, args_directional, sample_idx=5, channel_idx=0)

        # Run comparison with directional performance
        if 'performance' in locals():
            compare_regression_vs_directional(performance)
        else:
            print(
                "⚠️ Directional performance not calculated yet. Run directional training cell first.")
    else:
        print("⚠️ Directional results not available. Run directional training cell first.")
        # Still run comparison without directional performance
        compare_regression_vs_directional()

except NameError as e:
    print(f"⚠️ Some variables not defined: {e}")
    print("📝 Make sure to run the directional training cell above first.")
    # Run basic comparison
    compare_regression_vs_directional()

⚠️ Directional results not available. Run directional training cell first.

📊 REGRESSION vs DIRECTIONAL COMPARISON

🔢 Standard Regression Performance:
   MAE: 0.087396
   MSE: 0.016238
   RMSE: 0.127427
test 3480
Use CPU


⚠️ Directional results not available. Run directional training cell first.

📊 REGRESSION vs DIRECTIONAL COMPARISON

🔢 Standard Regression Performance:
   MAE: 0.087396
   MSE: 0.016238
   RMSE: 0.127427
test 3480
Use CPU


⚠️ Directional results not available. Run directional training cell first.

📊 REGRESSION vs DIRECTIONAL COMPARISON

🔢 Standard Regression Performance:
   MAE: 0.087396
   MSE: 0.016238
   RMSE: 0.127427
test 3480
Use CPU


🔍 Running directional inference...


⚠️ Directional results not available. Run directional training cell first.

📊 REGRESSION vs DIRECTIONAL COMPARISON

🔢 Standard Regression Performance:
   MAE: 0.087396
   MSE: 0.016238
   RMSE: 0.127427
test 3480
Use CPU


🔍 Running directional inference...


RuntimeError: expected m1 and m2 to have the same dtype, but got: double != float

In [ ]:

exp = Exp_Main(args)

print(f'Args for this run: {vars(args)}')

best_model = exp.train(args.model_id)

Use CPU


Args for this run: {'is_training': 1, 'train_only': False, 'model_id': 'ETTh1_Pred_Notebook_Untuned', 'model': 'xPatch', 'data': 'custom', 'scale': True, 'root_path': './data/', 'data_path': 'ETTh1.csv', 'features': 'MS', 'target': 'OT', 'freq': 'h', 'checkpoints': './checkpoints/', 'embed': 'timeF', 'seq_len': 48, 'label_len': 48, 'pred_len': 5, 'enc_in': 7, 'patch_len': 12, 'stride': 6, 'padding_patch': 'end', 'ma_type': 'ema', 'alpha': 0.2, 'beta': 0.2, 'num_workers': 8, 'itr': 1, 'train_epochs': 3, 'batch_size': 16, 'patience': 15, 'learning_rate': 0.0001, 'des': 'Notebook_Run_MS', 'loss': 'mae', 'lradj': 'type1', 'revin': 1, 'use_gpu': False, 'gpu': 0, 'use_multi_gpu': False, 'devices': '0', 'test_flop': False, 'use_wandb': True, 'wandb_entity': 'xplstm', 'wandb_project': 'CS7643-GroupProject', 'experiment_notes': 'LSTM head after patching layer', 'd_model': 128, 'd_ff': 256, 'e_layers': 3, 'dropout': 0.1, 'k': 3, 'decomp': 0, 'use_lstm': True, 'lstm_hidden_size': 192, 'lstm_layer

In [ ]:
print(args.model_id)
exp.test(args.model_id)

ETTh1_Pred_Notebook_Untuned
test 3480
[[[-1.4728129]
  [-1.4929314]
  [-1.5069768]
  [-1.5064385]
  [-1.504241 ]]

 [[-1.4854307]
  [-1.4985139]
  [-1.5105591]
  [-1.5047836]
  [-1.5216317]]

 [[-1.508234 ]
  [-1.5192217]
  [-1.5340004]
  [-1.5249159]
  [-1.5457389]]

 [[-1.4673293]
  [-1.4762927]
  [-1.4935752]
  [-1.4896475]
  [-1.5009961]]

 [[-1.5006298]
  [-1.5071477]
  [-1.5290128]
  [-1.5131284]
  [-1.5302775]]

 [[-1.525568 ]
  [-1.5197366]
  [-1.5506454]
  [-1.5293376]
  [-1.5425771]]

 [[-1.501866 ]
  [-1.4992138]
  [-1.5248911]
  [-1.504822 ]
  [-1.5194774]]

 [[-1.4062645]
  [-1.4148962]
  [-1.4225032]
  [-1.4136448]
  [-1.4288139]]

 [[-1.4432042]
  [-1.4385786]
  [-1.4597044]
  [-1.4498783]
  [-1.4416813]]

 [[-1.4958688]
  [-1.4857061]
  [-1.4975401]
  [-1.4728569]
  [-1.5058864]]

 [[-1.408861 ]
  [-1.3996578]
  [-1.4100335]
  [-1.4029303]
  [-1.4179107]]

 [[-1.4022557]
  [-1.407635 ]
  [-1.4142112]
  [-1.4065899]
  [-1.4091055]]

 [[-1.4471184]
  [-1.4499176]
  [-1.46

In [ ]:
folder_path = os.path.join('./test_results/', args.model_id + '/')
predictions_path = os.path.join(folder_path, 'pred.npy')
trues_path = os.path.join(folder_path, 'true.npy')

if os.path.exists(predictions_path) and os.path.exists(trues_path):
    all_preds = np.load(predictions_path)
    all_trues = np.load(trues_path)

    import matplotlib.pyplot as plt

    sample_idx = 10  # Pick a sample to visualize

    plt.figure(figsize=(12, 6))
    plt.plot(all_trues[sample_idx, :, 0], label='Ground Truth')
    plt.plot(all_preds[sample_idx, :, 0], label='Prediction')
    plt.title(f'Sample {sample_idx} Prediction vs Ground Truth (Last Channel)')
    plt.xlabel('Time Step (future days)')
    plt.ylabel('Price')
    plt.legend()
    plt.grid(False)
    plt.show()

else:
    print("Prediction and true value files not found. Ensure test() ran successfully.")

#### **Bellow:** Alternative training configuration with sweeps (hyperparameter tuning by wandb). Run in alternative to the above training loop.

In [ ]:
# Complete sweep cell for notebook
import wandb


def notebook_sweep():
    # Advanced sweep config
    sweep_config = {
        'method': 'bayes',
        'metric': {
            'name': 'final_test_mse',
            'goal': 'minimize'
        },
        'parameters': {
            # Learning optimization
            'learning_rate': {
                'distribution': 'log_uniform_values',
                'min': 0.00001,
                'max': 0.001
            },
            'batch_size': {'values': [8, 16, 32]},  # Reduced range
            'train_epochs': {'values': [3, 5, 8]},  # Reduced range

            # Model architecture - xPatch specific
            'd_model': {'values': [64, 128, 256]},  # Reduced range
            # Fixed values instead of distribution
            'd_ff': {'values': [128, 256, 512, 768]},
            'e_layers': {'values': [2, 3, 4]},  # Reduced range
            'dropout': {
                'distribution': 'uniform',
                'min': 0.1,
                'max': 0.3
            },

            # Patching strategy - MORE CONSERVATIVE
            # Reduced range, avoiding very small/large
            'patch_len': {'values': [8, 12, 16]},
            'stride': {'values': [4, 6, 8]},  # Reduced range

            # Sequence modeling - CONSERVATIVE
            'seq_len': {'values': [48, 72, 96]},  # Reduced range
            'pred_len': {'values': [3, 5, 7]},    # Reduced range

            # Moving average parameters
            'ma_type': {'values': ['ema', 'dema']},
            'alpha': {
                'distribution': 'uniform',
                'min': 0.1,
                'max': 0.4
            },
            'beta': {
                'distribution': 'uniform',
                'min': 0.1,
                'max': 0.4
            },

            # Advanced xPatch parameters
            'k': {'values': [2, 3, 4]},  # Reduced range
            'decomp': {'values': [0, 1]},

            # Learning rate scheduling
            # Removed 'cosine' temporarily
            'lradj': {'values': ['type1', 'type2']},

            # Regularization
            'revin': {'values': [0, 1]},  # Reduced range

            # Loss function variants
            'loss_weight_decay': {
                'distribution': 'uniform',
                'min': 0.5,
                'max': 2.0
            }
        },

        # Advanced early termination
        'early_terminate': {
            'type': 'hyperband',
            'min_iter': 2,
            'max_iter': 15,
            'eta': 3,
            's': 2
        }
    }

    # Create sweep
    sweep_id = wandb.sweep(sweep_config,
                           project="CS7643-GroupProject",
                           entity="xplstm")

    def train_run():
        # Define Args class inside the function so it's available
        class Args:
            def __init__(self):
                self.is_training = 1
                self.train_only = False
                self.model_id = 'AAPL_Pred5_Notebook_Tuned'
                self.model = 'xPatch'
                self.data = 'custom'
                self.scale = True
                self.root_path = './data/'
                self.data_path = 'ETTh1.csv'
                self.features = 'MS'
                self.target = 'OT'
                self.freq = 'h'
                self.checkpoints = './checkpoints/'
                self.embed = 'timeF'
                self.label_len = 48
                self.enc_in = 7
                self.padding_patch = 'end'
                self.num_workers = 8
                self.itr = 1
                self.patience = 15
                self.des = 'Sweep_Run'
                self.loss = 'mae'
                self.revin = 1

                # Default values (will be overridden by sweep)
                self.seq_len = 48
                self.pred_len = 5
                self.patch_len = 12
                self.stride = 6
                self.ma_type = 'ema'
                self.alpha = 0.2
                self.beta = 0.2
                self.train_epochs = 3
                self.batch_size = 16
                self.learning_rate = 0.0001
                self.lradj = 'type1'
                self.d_model = 128
                self.d_ff = 256
                self.e_layers = 3
                self.dropout = 0.1
                self.k = 3
                self.decomp = 0

                # GPU settings
                self.use_gpu = True if torch.cuda.is_available() else False
                self.gpu = 0
                self.use_multi_gpu = False
                self.devices = '0'
                self.test_flop = False

                # Wandb settings
                self.use_wandb = True
                self.wandb_entity = 'xplstm'
                self.wandb_project = 'CS7643-GroupProject'
                self.experiment_notes = 'Sweep experiment'

        wandb.init()

        try:
            # Create Args instance
            args = Args()

            # Override all sweep parameters
            for param, value in wandb.config.items():
                if hasattr(args, param):
                    setattr(args, param, value)

            # Ensure model_id is unique
            args.model_id = f"sweep_{wandb.run.name}"

            # Advanced parameter validation and adjustment
            # Ensure stride <= patch_len
            if args.stride > args.patch_len:
                args.stride = args.patch_len // 2
                wandb.log(
                    {"param_adjustment": f"stride adjusted to {args.stride}"})

            # Ensure d_ff >= d_model
            if args.d_ff < args.d_model:
                args.d_ff = args.d_model * 2
                wandb.log({"param_adjustment": f"d_ff adjusted to {args.d_ff}"})

            # Ensure pred_len < seq_len
            if args.pred_len >= args.seq_len:
                args.pred_len = min(args.pred_len, args.seq_len // 4)
                wandb.log(
                    {"param_adjustment": f"pred_len adjusted to {args.pred_len}"})

            # Log parameter combinations for analysis
            wandb.log({
                "config/patch_ratio": args.patch_len / args.seq_len,
                "config/stride_ratio": args.stride / args.patch_len,
                "config/model_complexity": args.d_model * args.e_layers,
                "config/ff_ratio": args.d_ff / args.d_model,
                "config/prediction_horizon": args.pred_len / args.seq_len
            })

            # Add error handling for configuration issues
            if args.patch_len <= 0 or args.stride <= 0:
                raise ValueError(
                    f"Invalid patch configuration: patch_len={args.patch_len}, stride={args.stride}")

            if args.d_model <= 0 or args.d_ff <= 0:
                raise ValueError(
                    f"Invalid model dimensions: d_model={args.d_model}, d_ff={args.d_ff}")

            if not os.path.exists(args.checkpoints):
                os.makedirs(args.checkpoints)

            print(f"Starting sweep run: {args.model_id}")
            print(f"Key parameters: lr={args.learning_rate:.6f}, batch={args.batch_size}, "
                  f"patch_len={args.patch_len}, d_model={args.d_model}")

            # Create experiment and train
            exp = Exp_Main(args)
            best_model = exp.train(args.model_id)
            exp.test(args.model_id)

            # Log success
            wandb.log({"run_status": "completed"})

        except Exception as e:
            print(f"Error in sweep run: {str(e)}")
            wandb.log({
                "run_status": "failed",
                "error_message": str(e),
                "final_test_mse": float('inf')  # Ensure bad runs are penalized
            })
            raise e

    print(
        f"Sweep URL: https://wandb.ai/xplstm/CS7643-GroupProject/sweeps/{sweep_id}")
    print("Advanced sweep configuration:")
    print(f"- {len(sweep_config['parameters'])} hyperparameters")
    print(f"- Bayesian optimization with Hyperband early termination")
    print(f"- Parameter validation and auto-adjustment")

    # Run sweep with more experiments for comprehensive search
    wandb.agent(sweep_id, function=train_run, count=3)

    return sweep_id


# Uncomment to run advanced sweep
sweep_id = notebook_sweep()

Create sweep with ID: 721yad0v
Sweep URL: https://wandb.ai/xplstm/CS7643-GroupProject/sweeps/721yad0v
Sweep URL: https://wandb.ai/xplstm/CS7643-GroupProject/sweeps/721yad0v
Advanced sweep configuration:
- 19 hyperparameters
- Bayesian optimization with Hyperband early termination
- Parameter validation and auto-adjustment


wandb: Agent Starting Run: ke9z36dj with config:
wandb: 	alpha: 0.20477411451465136
wandb: 	batch_size: 32
wandb: 	beta: 0.25398474044277786
wandb: 	d_ff: 512
wandb: 	d_model: 128
wandb: 	decomp: 1
wandb: 	dropout: 0.24739758628144495
wandb: 	e_layers: 4
wandb: 	k: 3
wandb: 	learning_rate: 0.0002293135929709356
wandb: 	loss_weight_decay: 0.8358802964194618
wandb: 	lradj: type1
wandb: 	ma_type: dema
wandb: 	patch_len: 16
wandb: 	pred_len: 5
wandb: 	revin: 1
wandb: 	seq_len: 96
wandb: 	stride: 8
wandb: 	train_epochs: 3


Starting sweep run: sweep_likely-sweep-1
Key parameters: lr=0.000229, batch=32, patch_len=16, d_model=128
Use CPU
Error in sweep run: 'float' object has no attribute 'to'


wandb: ERROR Run ke9z36dj errored:
wandb: ERROR Traceback (most recent call last):
wandb: ERROR   File "/usr/local/python/3.12.1/lib/python3.12/site-packages/wandb/agents/pyagent.py", line 302, in _run_job
wandb: ERROR     self._function()
wandb: ERROR   File "/tmp/ipykernel_9542/2736668503.py", line 213, in train_run
wandb: ERROR     raise e
wandb: ERROR   File "/tmp/ipykernel_9542/2736668503.py", line 199, in train_run
wandb: ERROR     exp = Exp_Main(args)
wandb: ERROR           ^^^^^^^^^^^^^^
wandb: ERROR   File "/workspaces/Finance-Time-Series-Forcasting/exp/exp_main.py", line 22, in __init__
wandb: ERROR     super(Exp_Main, self).__init__(args)
wandb: ERROR   File "/workspaces/Finance-Time-Series-Forcasting/exp/exp_basic.py", line 10, in __init__
wandb: ERROR     self.model = self._build_model().to(self.device)
wandb: ERROR                  ^^^^^^^^^^^^^^^^^^^
wandb: ERROR   File "/workspaces/Finance-Time-Series-Forcasting/exp/exp_main.py", line 40, in _build_model
wandb: ERROR   

Starting sweep run: sweep_quiet-sweep-2
Key parameters: lr=0.000202, batch=32, patch_len=16, d_model=256
Use CPU


train 12092
val 1736
test 3478
	iters: 100, epoch: 1 | loss: 0.3392132
	speed: 0.0138s/iter; left time: 40.3113s
	iters: 200, epoch: 1 | loss: 0.2884287
	speed: 0.0122s/iter; left time: 34.3627s
	iters: 300, epoch: 1 | loss: 0.3368687
	speed: 0.0121s/iter; left time: 32.9613s
Epoch: 1 cost time: 4.803227424621582
Epoch: 1, Steps: 377 | Train Loss: 0.3395828 Vali Loss: 0.4639564 Test Loss: 0.3872925
Validation loss decreased (inf --> 0.463956).  Saving model ...
	iters: 100, epoch: 2 | loss: 0.2141321
	speed: 0.0346s/iter; left time: 87.8965s
	iters: 200, epoch: 2 | loss: 0.1845696
	speed: 0.0125s/iter; left time: 30.5577s
	iters: 300, epoch: 2 | loss: 0.2750836
	speed: 0.0123s/iter; left time: 28.7398s
Epoch: 2 cost time: 4.917123794555664
Epoch: 2, Steps: 377 | Train Loss: 0.2116692 Vali Loss: 0.3454794 Test Loss: 0.1796886
Validation loss decreased (0.463956 --> 0.345479).  Saving model ...
Updating learning rate to 5e-05
	iters: 100, epoch: 3 | loss: 0.1627022
	speed: 0.0354s/iter; 

wandb: Ctrl + C detected. Stopping sweep.


Exception in thread Thread-69 (_run_job):
Traceback (most recent call last):
  File "/tmp/ipykernel_9542/2736668503.py", line 200, in train_run
  File "/workspaces/Finance-Time-Series-Forcasting/exp/exp_main.py", line 166, in train
    for i, (batch_x, batch_y, batch_x_mark, batch_y_mark) in enumerate(train_loader):
  File "/home/codespace/.local/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 733, in __next__
    data = self._next_data()
           ^^^^^^^^^^^^^^^^^
  File "/home/codespace/.local/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1491, in _next_data
    idx, data = self._get_data()
                ^^^^^^^^^^^^^^^^
  File "/home/codespace/.local/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1453, in _get_data
    success, data = self._try_get_data()
                    ^^^^^^^^^^^^^^^^^^^^
  File "/home/codespace/.local/lib/python3.12/site-packages/torch/utils/data/dataloader.py", line 1284, in _try_get_data
    d

Error in sweep run: [Errno 2] No such file or directory


In [ ]:
# Complete sweep cell for notebook
import wandb


def notebook_sweep():
    # Advanced sweep config
    sweep_config = {
        'method': 'bayes',
        'metric': {
            'name': 'final_test_mse',
            'goal': 'minimize'
        },
        'parameters': {
            # Learning optimization
            'learning_rate': {
                'distribution': 'log_uniform_values',
                'min': 0.00001,
                'max': 0.001
            },
            'batch_size': {'values': [8, 16, 32]},  # Reduced range
            'train_epochs': {'values': [3, 5, 8]},  # Reduced range

            # Model architecture - xPatch specific
            'd_model': {'values': [64, 128, 256]},  # Reduced range
            # Fixed values instead of distribution
            'd_ff': {'values': [128, 256, 512, 768]},
            'e_layers': {'values': [2, 3, 4]},  # Reduced range
            'dropout': {
                'distribution': 'uniform',
                'min': 0.1,
                'max': 0.3
            },

            # Patching strategy - MORE CONSERVATIVE
            # Reduced range, avoiding very small/large
            'patch_len': {'values': [8, 12, 16]},
            'stride': {'values': [4, 6, 8]},  # Reduced range

            # Sequence modeling - CONSERVATIVE
            'seq_len': {'values': [48, 72, 96]},  # Reduced range
            'pred_len': {'values': [3, 5, 7]},    # Reduced range

            # Moving average parameters
            'ma_type': {'values': ['ema', 'dema']},
            'alpha': {
                'distribution': 'uniform',
                'min': 0.1,
                'max': 0.4
            },
            'beta': {
                'distribution': 'uniform',
                'min': 0.1,
                'max': 0.4
            },

            # Advanced xPatch parameters
            'k': {'values': [2, 3, 4]},  # Reduced range
            'decomp': {'values': [0, 1]},

            # Learning rate scheduling
            # Removed 'cosine' temporarily
            'lradj': {'values': ['type1', 'type2']},

            # Regularization
            'revin': {'values': [0, 1]},  # Reduced range

            # Loss function variants
            'loss_weight_decay': {
                'distribution': 'uniform',
                'min': 0.5,
                'max': 2.0
            }
        },

        # Advanced early termination
        'early_terminate': {
            'type': 'hyperband',
            'min_iter': 2,
            'max_iter': 15,
            'eta': 3,
            's': 2
        }
    }

    # Create sweep
    sweep_id = wandb.sweep(sweep_config,
                           project="CS7643-GroupProject",
                           entity="xplstm")

    def train_run():
        # Define Args class inside the function so it's available
        class Args:
            def __init__(self):
                self.is_training = 1
                self.train_only = False
                self.model_id = 'AAPL_Pred5_Notebook_Tuned'
                self.model = 'xPatch'
                self.data = 'custom'
                self.scale = True
                self.root_path = './data/'
                self.data_path = 'ETTh1.csv'
                self.features = 'MS'
                self.target = 'OT'
                self.freq = 'h'
                self.checkpoints = './checkpoints/'
                self.embed = 'timeF'
                self.label_len = 48
                self.enc_in = 7
                self.padding_patch = 'end'
                self.num_workers = 8
                self.itr = 1
                self.patience = 15
                self.des = 'Sweep_Run'
                self.loss = 'mae'
                self.revin = 1

                # Default values (will be overridden by sweep)
                self.seq_len = 48
                self.pred_len = 5
                self.patch_len = 12
                self.stride = 6
                self.ma_type = 'ema'
                self.alpha = 0.2
                self.beta = 0.2
                self.train_epochs = 3
                self.batch_size = 16
                self.learning_rate = 0.0001
                self.lradj = 'type1'
                self.d_model = 128
                self.d_ff = 256
                self.e_layers = 3
                self.dropout = 0.1
                self.k = 3
                self.decomp = 0

                # GPU settings
                self.use_gpu = True if torch.cuda.is_available() else False
                self.gpu = 0
                self.use_multi_gpu = False
                self.devices = '0'
                self.test_flop = False

                # Wandb settings
                self.use_wandb = True
                self.wandb_entity = 'xplstm'
                self.wandb_project = 'CS7643-GroupProject'
                self.experiment_notes = 'Sweep experiment'

        # Initialize wandb run
        run = wandb.init()

        try:
            # Create Args instance
            args = Args()

            # Override all sweep parameters
            for param, value in wandb.config.items():
                if hasattr(args, param):
                    setattr(args, param, value)

            # Ensure model_id is unique
            args.model_id = f"sweep_{wandb.run.name}"

            # CRITICAL: Enhanced parameter validation and adjustment
            # 1. Ensure patch_len is reasonable for seq_len
            if args.patch_len > args.seq_len:
                args.patch_len = args.seq_len // 4
                wandb.log(
                    {"param_adjustment": f"patch_len adjusted to {args.patch_len}"})

            # 2. Ensure stride is reasonable for patch_len
            if args.stride > args.patch_len:
                args.stride = max(1, args.patch_len // 2)
                wandb.log(
                    {"param_adjustment": f"stride adjusted to {args.stride}"})

            # 3. Calculate number of patches and ensure it's > 0
            num_patches = max(
                1, (args.seq_len - args.patch_len) // args.stride + 1)
            if num_patches <= 0:
                # Adjust parameters to ensure at least 1 patch
                args.patch_len = min(args.patch_len, args.seq_len)
                args.stride = min(args.stride, args.patch_len)
                num_patches = max(
                    1, (args.seq_len - args.patch_len) // args.stride + 1)
                wandb.log({
                    "param_adjustment": f"Fixed patching: patch_len={args.patch_len}, stride={args.stride}, num_patches={num_patches}"
                })

            # 4. Ensure d_ff >= d_model
            if args.d_ff < args.d_model:
                args.d_ff = args.d_model * 2
                wandb.log({"param_adjustment": f"d_ff adjusted to {args.d_ff}"})

            # 5. Ensure pred_len < seq_len
            if args.pred_len >= args.seq_len:
                args.pred_len = min(args.pred_len, args.seq_len // 4)
                wandb.log(
                    {"param_adjustment": f"pred_len adjusted to {args.pred_len}"})

            # 6. Additional validation for xPatch specific parameters
            if args.patch_len < 4:
                args.patch_len = 4
                wandb.log(
                    {"param_adjustment": f"patch_len minimum adjusted to {args.patch_len}"})

            if args.stride < 1:
                args.stride = 1
                wandb.log(
                    {"param_adjustment": f"stride minimum adjusted to {args.stride}"})

            # 7. Validate the final configuration
            final_num_patches = (
                args.seq_len - args.patch_len) // args.stride + 1
            if final_num_patches <= 0:
                raise ValueError(f"Invalid configuration results in {final_num_patches} patches. "
                                 f"seq_len={args.seq_len}, patch_len={args.patch_len}, stride={args.stride}")

            # Log parameter combinations for analysis
            wandb.log({
                "config/patch_ratio": args.patch_len / args.seq_len,
                "config/stride_ratio": args.stride / args.patch_len,
                "config/model_complexity": args.d_model * args.e_layers,
                "config/ff_ratio": args.d_ff / args.d_model,
                "config/prediction_horizon": args.pred_len / args.seq_len,
                "config/num_patches": final_num_patches,
                "config/patch_coverage": (args.patch_len + (final_num_patches - 1) * args.stride) / args.seq_len
            })

            # Add error handling for configuration issues
            if args.patch_len <= 0 or args.stride <= 0:
                raise ValueError(
                    f"Invalid patch configuration: patch_len={args.patch_len}, stride={args.stride}")

            if args.d_model <= 0 or args.d_ff <= 0:
                raise ValueError(
                    f"Invalid model dimensions: d_model={args.d_model}, d_ff={args.d_ff}")

            if not os.path.exists(args.checkpoints):
                os.makedirs(args.checkpoints)

            print(f"Starting sweep run: {args.model_id}")
            print(f"Key parameters: lr={args.learning_rate:.6f}, batch={args.batch_size}, "
                  f"patch_len={args.patch_len}, d_model={args.d_model}")
            print(f"Patching info: seq_len={args.seq_len}, patch_len={args.patch_len}, "
                  f"stride={args.stride}, num_patches={final_num_patches}")

            # Create experiment and train
            exp = Exp_Main(args)
            best_model = exp.train(args.model_id)
            exp.test(args.model_id)

            # Log success
            if wandb.run is not None:
                wandb.log({"run_status": "completed"})

        except Exception as e:
            print(f"Error in sweep run: {str(e)}")
            # More robust error logging
            try:
                if wandb.run is not None:
                    wandb.log({
                        "run_status": "failed",
                        "error_message": str(e),
                        # Ensure bad runs are penalized
                        "final_test_mse": float('inf')
                    })
            except:
                print("Could not log error to wandb")

            # Don't re-raise the exception - just let the run fail gracefully
            return

        finally:
            # Ensure wandb run is properly finished
            if wandb.run is not None:
                wandb.finish()

    print(
        f"Sweep URL: https://wandb.ai/xplstm/CS7643-GroupProject/sweeps/{sweep_id}")
    print("Advanced sweep configuration:")
    print(f"- {len(sweep_config['parameters'])} hyperparameters")
    print(f"- Bayesian optimization with Hyperband early termination")
    print(f"- Parameter validation and auto-adjustment")

    # Run sweep with more experiments for comprehensive search
    wandb.agent(sweep_id, function=train_run, count=3)

    return sweep_id


# Uncomment to run advanced sweep
sweep_id = notebook_sweep()

Create sweep with ID: dfs0bz1y
Sweep URL: https://wandb.ai/xplstm/CS7643-GroupProject/sweeps/dfs0bz1y
Sweep URL: https://wandb.ai/xplstm/CS7643-GroupProject/sweeps/dfs0bz1y
Advanced sweep configuration:
- 19 hyperparameters
- Bayesian optimization with Hyperband early termination
- Parameter validation and auto-adjustment


wandb: Agent Starting Run: 44kjaaml with config:
wandb: 	alpha: 0.1329597357733036
wandb: 	batch_size: 32
wandb: 	beta: 0.29378334377376036
wandb: 	d_ff: 128
wandb: 	d_model: 128
wandb: 	decomp: 1
wandb: 	dropout: 0.19092579130934695
wandb: 	e_layers: 3
wandb: 	k: 3
wandb: 	learning_rate: 4.31697164823031e-05
wandb: 	loss_weight_decay: 0.5070863549376494
wandb: 	lradj: type2
wandb: 	ma_type: ema
wandb: 	patch_len: 16
wandb: 	pred_len: 7
wandb: 	revin: 1
wandb: 	seq_len: 96
wandb: 	stride: 4
wandb: 	train_epochs: 8


Starting sweep run: sweep_cool-sweep-1
Key parameters: lr=0.000043, batch=32, patch_len=16, d_model=128
Patching info: seq_len=96, patch_len=16, stride=4, num_patches=21
Use CPU


train 12092
val 1736
test 3478
	iters: 100, epoch: 1 | loss: 0.1387980
	speed: 0.0227s/iter; left time: 66.2229s
	iters: 200, epoch: 1 | loss: 0.1189318
	speed: 0.0203s/iter; left time: 57.0536s
	iters: 300, epoch: 1 | loss: 0.1338258
	speed: 0.0199s/iter; left time: 53.9567s
Epoch: 1 cost time: 7.989301443099976
Epoch: 1, Steps: 377 | Train Loss: 0.1391927 Vali Loss: 0.0708973 Test Loss: 0.0510343
Validation loss decreased (inf --> 0.070897).  Saving model ...
	iters: 100, epoch: 2 | loss: 0.1333826
	speed: 0.0515s/iter; left time: 130.9004s
	iters: 200, epoch: 2 | loss: 0.0943144
	speed: 0.0199s/iter; left time: 48.5061s
	iters: 300, epoch: 2 | loss: 0.0900629
	speed: 0.0194s/iter; left time: 45.3046s
Epoch: 2 cost time: 7.715447425842285
Epoch: 2, Steps: 377 | Train Loss: 0.0993500 Vali Loss: 0.0536858 Test Loss: 0.0338554
Validation loss decreased (0.070897 --> 0.053686).  Saving model ...
Updating learning rate to 5e-05
	iters: 100, epoch: 3 | loss: 0.0865256
	speed: 0.0496s/iter;

wandb: Agent Starting Run: 331hgjyj with config:
wandb: 	alpha: 0.25947374214422514
wandb: 	batch_size: 8
wandb: 	beta: 0.23461385902220108
wandb: 	d_ff: 128
wandb: 	d_model: 256
wandb: 	decomp: 1
wandb: 	dropout: 0.1419477954094698
wandb: 	e_layers: 2
wandb: 	k: 2
wandb: 	learning_rate: 3.123140127628863e-05
wandb: 	loss_weight_decay: 1.5704356395080463
wandb: 	lradj: type2
wandb: 	ma_type: ema
wandb: 	patch_len: 8
wandb: 	pred_len: 7
wandb: 	revin: 1
wandb: 	seq_len: 72
wandb: 	stride: 8
wandb: 	train_epochs: 3


Starting sweep run: sweep_glamorous-sweep-2
Key parameters: lr=0.000031, batch=8, patch_len=8, d_model=256
Patching info: seq_len=72, patch_len=8, stride=8, num_patches=9
Use CPU


train 12116
val 1736
test 3478
	iters: 100, epoch: 1 | loss: 0.1917458
	speed: 0.0092s/iter; left time: 40.8517s
	iters: 200, epoch: 1 | loss: 0.1733142
	speed: 0.0075s/iter; left time: 32.3996s
	iters: 300, epoch: 1 | loss: 0.0871408
	speed: 0.0066s/iter; left time: 27.8576s
	iters: 400, epoch: 1 | loss: 0.2151660
	speed: 0.0072s/iter; left time: 29.6688s
	iters: 500, epoch: 1 | loss: 0.1230252
	speed: 0.0071s/iter; left time: 28.5714s
	iters: 600, epoch: 1 | loss: 0.1557723
	speed: 0.0071s/iter; left time: 27.8080s
	iters: 700, epoch: 1 | loss: 0.1112086
	speed: 0.0068s/iter; left time: 25.9453s
	iters: 800, epoch: 1 | loss: 0.2216544
	speed: 0.0068s/iter; left time: 25.3074s
	iters: 900, epoch: 1 | loss: 0.1283960
	speed: 0.0066s/iter; left time: 24.0575s
	iters: 1000, epoch: 1 | loss: 0.1465994
	speed: 0.0067s/iter; left time: 23.6444s
	iters: 1100, epoch: 1 | loss: 0.1248783
	speed: 0.0067s/iter; left time: 22.9196s
	iters: 1200, epoch: 1 | loss: 0.0978145
	speed: 0.0066s/iter; le

wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: u7uwns7i with config:
wandb: 	alpha: 0.17858413918976151
wandb: 	batch_size: 16
wandb: 	beta: 0.3787823853018955
wandb: 	d_ff: 512
wandb: 	d_model: 256
wandb: 	decomp: 0
wandb: 	dropout: 0.2672522657727061
wandb: 	e_layers: 3
wandb: 	k: 3
wandb: 	learning_rate: 0.00014641657039420427
wandb: 	loss_weight_decay: 0.9245550247129026
wandb: 	lradj: type2
wandb: 	ma_type: dema
wandb: 	patch_len: 12
wandb: 	pred_len: 7
wandb: 	revin: 0
wandb: 	seq_len: 96
wandb: 	stride: 4
wandb: 	train_epochs: 8


Starting sweep run: sweep_icy-sweep-3
Key parameters: lr=0.000146, batch=16, patch_len=12, d_model=256
Patching info: seq_len=96, patch_len=12, stride=4, num_patches=22
Use CPU
Error in sweep run: 'float' object has no attribute 'to'
